In [1]:
%matplotlib inline

from pygenn.genn_model import (GeNNModel,
                               create_custom_neuron_class,
                               create_custom_weight_update_class,
                               create_dpf_class,
                               create_custom_init_var_snippet_class,
                               init_var,
                               create_var_ref)

from neurons import Lif, External, Noise
import synapses
from dynsys import damped_spring_mass
from utils import norm_w_no_autapse_model, EulerMaruyama

from scipy.integrate import solve_ivp
from scipy.linalg import solve_continuous_are as riccati

import numpy as np

from tqdm import tqdm

import matplotlib.pyplot as plt

import ipdb

In [2]:
np.random.seed(12)

In [5]:
######################## Simulation Parameters
T = 30.0
DT = 0.02
NT = int(T / DT)
T = NT * DT

t_ax = np.arange(NT) * DT

In [6]:
######################## Network Parameters
N = 100
NDS = 2
K = 2
NZ = 50
KZ = 2

In [7]:
## Noise
# SIGM_NOISE_LIF is a covariance matrix
# that summarises the effect of both the
# noise term mu_v and the indirect noise term mu_n.
# If the respective covariances are
# C_v, C_n and C_nv (cross-covariance),
# the combined covariance should be
# C_v + F_k C_nv + (F_k C_nv)^T + F C_n F^T
# (If I did the math correctly)
SIGM_NOISE_N = 1e-4*np.identity(NDS)

SIGM_NOISE_D = 1e-4*np.identity(NDS)


SIGM_NOISE_LIF = np.eye(N)*0.1
# Calculate the projection matrix P_NOISE
# that generates this covariance
# from uncorrelated N-dimensional
# zero-mean noise.
u,s,v = np.linalg.svd(SIGM_NOISE_LIF)
P_NOISE = u @ np.diag(np.sqrt(s))

In [8]:
D = np.random.randn(K,N) # decoding matrix
D = D / np.sqrt(np.diag(D.T@D)) # normalize vectors
D = D/50 # reduce size
T = np.diag(D.T@D)/2

Dz = np.random.randn(KZ,NZ)
Dz = Dz / np.sqrt(np.diag(Dz.T@Dz)) # normalize vectors
Dz = Dz/50 # reduce size
Tz = np.diag(Dz.T@Dz)/2

In [9]:
######## lin system + control
m = 20.
k = 6.
c = 2.

w = np.sqrt(k/m)
damp = c/(2 * m * w)

A = np.array([[0, 1],
              [-w**2, -2*damp*w]])

B = np.array([[0, 1]]).T

x = np.ones((NDS, NT+1))
u = np.zeros((NDS, NT+1))


f = lambda tf, xf: lin_system(xf, u=u, A=A, B=B)

ds_integrator = EulerMaruyama(f, SIGM_NOISE_D, DT, NDS,
                                buffer_rand_samples=NT)

x[:,0] = np.array([3, 0])

z = np.empty([2, NT+1])
z[:, :int(NT/4)] = np.outer(np.array([0, 0]), np.ones(int(NT/4)))
z[:, int(NT/4):int(NT/2)] = np.outer(np.array([1, 0]), np.ones(int(NT/4)))
z[:, int(NT/2):int(3*NT/4)] = np.outer(np.array([2, 0]), np.ones(int(NT/4)))
z[:, int(3*NT/4):] = np.outer(np.array([1, 0]), np.ones(int(NT/4)+1))
z_dot = np.zeros([K, NT+1])

In [10]:
###### Connections
C = np.array([[1, 0], [0, 0]])
Q = np.identity(2)
Q[0, 0] = 10
R = 1e-2

X = riccati(A, B, Q, R)
K_r = R**(-1)*B.T@X

Y = riccati(A.T, C, SIGM_NOISE_D, SIGM_NOISE_D)
K_f = Y@C.T@SIGM_NOISE_D